[![Colab](https://colab.research.google.com/assets/colab-badge.svg)](https://colab.research.google.com/github/giswqs/notebook-share/blob/master/docs/pakistan_floods.ipynb)
[![Open in SageMaker Studio Lab](https://studiolab.sagemaker.aws/studiolab.svg)](https://studiolab.sagemaker.aws/import/github/giswqs/notebook-share/blob/master/docs/pakistan_floods.ipynb)
[![Open in Planetary Computer](https://img.shields.io/badge/Open-Planetary%20Computer-black?style=flat&logo=microsoft)](https://pccompute.westeurope.cloudapp.azure.com/compute/hub/user-redirect/git-pull?repo=https://github.com/giswqs/notebook-share&urlpath=lab/tree/notebook-share/docs/pakistan_floods.ipynb&branch=master)
[![Binder](https://mybinder.org/badge_logo.svg)](https://mybinder.org/v2/gh/giswqs/notebook-share/HEAD?labpath=docs%pakistan_floods.ipynb)

# Peru Floods 2022 Using Earth Engine and Geemap - Sentinel 1



## Import libraries

In [3]:
import ee
import geemap

In [4]:
country_name = 'Peru'
pre_flood_start_date = '2022-06-01' # dry season
pre_flood_end_date = '2022-9-30'
flood_start_date = '2023-02-01' # flooding period
flood_end_date = '2023-04-16'

## Create Sentinel-1 SAR composites

We can also use Sentinel-1 [Synthetic Aperture Radar (SAR)](https://www.earthdata.nasa.gov/learn/backgrounders/what-is-sar) data to extract flood extent. Radar can collect signals in different polarizations, by controlling the analyzed polarization in both the transmit and receive paths. Signals emitted in vertical (V) and received in horizontal (H) polarization would be indicated by a VH. Alternatively, a signal that was emitted in horizontal (H) and received in horizontal (H) would be indicated by HH, and so on. Examining the signal strength from these different polarizations carries information about the structure of the imaged surface. Rough surface scattering, such as that caused by bare soil or water, is most sensitive to VV scattering. Therefore, VV polarization is often used to detect water bodies. 

Sentinel-1 operates in four exclusive [acquisition modes](https://sentinels.copernicus.eu/web/sentinel/missions/sentinel-1/instrument-payload):

* Stripmap (SM)
* Interferometric Wide swath (IW)
* Extra-Wide swath (EW)
* Wave mode (WV)

The Interferometric Wide swath (IW) mode allows combining a large swath width (250 km) with a moderate geometric resolution (5 m by 20 m). The IW mode is the default acquisition mode over land. In this tutorial, we will use Sentinel-1 IW mode data to extract flood extent.

The [Sentinel-1 SAR data](https://developers.google.com/earth-engine/datasets/catalog/COPERNICUS_S1_GRD) are available from 2014 to present. Let's filter the `COPERNICUS/S1_GRD` dataset by the date range and location.

In [5]:
ee.Initialize()

In [6]:
# Get Peru bounds
country_name = 'Peru'

country = ee.FeatureCollection('USDOS/LSIB_SIMPLE/2017').filter(
    ee.Filter.eq('country_na', country_name)
)

local_boundary = ee.FeatureCollection('users/indybrownhall/peru')


# Pre-flood
s1_col_2022 = (
    ee.ImageCollection('COPERNICUS/S1_GRD')
    .filter(ee.Filter.listContains('transmitterReceiverPolarisation', 'VV'))
    .filter(ee.Filter.eq('instrumentMode', 'IW'))
    .filter(ee.Filter.eq('orbitProperties_pass', 'ASCENDING'))
    .filterDate(pre_flood_start_date, pre_flood_end_date)
    .filterBounds(country)
    .select('VV')
)

In [7]:
s1_col_2022

Create the Sentinel-1 image collection for the flood period.

In [8]:
# Flooding period
s1_col_2023 = (
    ee.ImageCollection('COPERNICUS/S1_GRD')
    .filter(ee.Filter.listContains('transmitterReceiverPolarisation', 'VV'))
    .filter(ee.Filter.eq('instrumentMode', 'IW'))
    .filter(ee.Filter.eq('orbitProperties_pass', 'ASCENDING'))
    .filterDate(flood_start_date, flood_end_date)
    .filterBounds(country)
    .select('VV')
)

In [9]:
s1_col_2023

Create Sentinel-1 SAR composites for the pre-flood and flood periods.

In [10]:
Map = geemap.Map()
Map.add_basemap('HYBRID')
sar_2022 = s1_col_2022.reduce(ee.Reducer.percentile([20])).clipToCollection(country)
sar_2023 = s1_col_2023.reduce(ee.Reducer.percentile([20])).clipToCollection(country)
Map.addLayer(sar_2022, {'min': -25, 'max': -5}, 'SAR 2022')
Map.addLayer(sar_2023, {'min': -25, 'max': -5}, 'SAR 2023')
Map.centerObject(country)
Map

Map(center=[20, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=HBox(children=(Togg…

## Apply speckle filtering

Speckle, appearing in synthetic aperture radar (SAR) images as granular noise, is due to the interference of waves reflected from many elementary scatterers. Speckle in SAR images complicates the image interpretation problem by reducing the effectiveness of image segmentation and classification ([Lee et al., 1994](https://doi.org/10.1080/02757259409532206)). Therefore, speckle filtering is often applied to SAR images to reduce the speckle noise. In this example, we apply a morphological speckle filter to the Sentinel-1 SAR images. The morphological speckle filter is a non-linear filter that uses the median value of a pixel and its neighboring pixels to replace the pixel value. The kernel size is set to 100 meters.

In [11]:
col_2022 = s1_col_2022.map(lambda img: img.focal_median(100, 'circle', 'meters'))
col_2023 = s1_col_2023.map(lambda img: img.focal_median(100, 'circle', 'meters'))

In [12]:
Map = geemap.Map()
Map.add_basemap('HYBRID')
sar_2022 = col_2022.reduce(ee.Reducer.percentile([20])).clipToCollection(country)
sar_2023 = col_2023.reduce(ee.Reducer.percentile([20])).clipToCollection(country)
Map.addLayer(sar_2022, {'min': -25, 'max': -5}, 'SAR 2022')
Map.addLayer(sar_2023, {'min': -25, 'max': -5}, 'SAR 2023')
Map.centerObject(country)
Map

Map(center=[20, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=HBox(children=(Togg…

## Extract SAR water extent

Water usually appears dark in SAR images because radar waves are reflected differently by different surfaces. Water is a smooth, flat surface that does not reflect radar waves very well, so it appears dark in SAR images. Thresholding SAR imagery is one of the most widely used approaches to delineate water extent for its effectiveness and efficiency ([Liang and Liu, 2020](https://doi.org/10.1016/j.isprsjprs.2019.10.017)). Thresholding methods can be generally divided into two categories: global and local. Global thresholding methods use a single threshold value to segment the entire image. Local thresholding methods use a different threshold value for each pixel. In this example, we use a global thresholding method to extract the water extent. The threshold value is set to -18 
dB.

In [13]:
threshold = -18
water_2022 = sar_2022.lt(threshold)
water_2023 = sar_2023.lt(threshold)

Create a split-view map to compare the pre-flood and flood water extent side by side.

In [14]:
Map = geemap.Map()
Map.setCenter(-81.5, -3.6, 7)

Map.addLayer(sar_2022, {'min': -25, 'max': -5}, 'SAR 2022')
Map.addLayer(sar_2023, {'min': -25, 'max': -5}, 'SAR 2023')

Map.addLayer(water_2022.selfMask(), {'palette': 'blue'}, 'Water 2022')
Map.addLayer(water_2023.selfMask(), {'palette': 'red'}, 'Water 2023')

style = {'color': 'black', 'fillColor': '00000000'}
Map.addLayer(country.style(**style), {}, country_name)
Map

Map(center=[-3.6, -81.5], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=HBox(children…

## Extract SAR flood extent

Similar to the Landsat approach, we can subtract the pre-flood water extent from the flood water extent to extract the flood extent.

In [15]:
flood_extent = water_2023.subtract(water_2022).gt(0).selfMask()

## reduce to vector
flood_extent_vector = flood_extent.reduceToVectors(
  reducer = ee.Reducer.countEvery(), 
  geometry = country,
  scale = 100,
  maxPixels = 1e10)

print(flood_extent_vector)

ee.FeatureCollection({
  "functionInvocationValue": {
    "functionName": "Image.reduceToVectors",
    "arguments": {
      "geometry": {
        "functionInvocationValue": {
          "functionName": "Collection.geometry",
          "arguments": {
            "collection": {
              "functionInvocationValue": {
                "functionName": "Collection.filter",
                "arguments": {
                  "collection": {
                    "functionInvocationValue": {
                      "functionName": "Collection.loadTable",
                      "arguments": {
                        "tableId": {
                          "constantValue": "USDOS/LSIB_SIMPLE/2017"
                        }
                      }
                    }
                  },
                  "filter": {
                    "functionInvocationValue": {
                      "functionName": "Filter.equals",
                      "arguments": {
                        "leftField": {
      

The flood extent is the difference between the flood water extent and the pre-flood water extent. In other words, pixels identified as water in the flood period but not in the pre-flood period are considered as flooded pixels, which are shown in cyan.

In [16]:
Map = geemap.Map()
Map.setCenter(-81.5, -3.6, 7)

Map.addLayer(sar_2022, {'min': -25, 'max': -5}, 'SAR 2022')
Map.addLayer(sar_2023, {'min': -25, 'max': -5}, 'SAR 2023')
Map.addLayer(flood_extent_vector, {}, 'flood_extent_vector')

Map.addLayer(flood_extent, {'palette': 'cyan'}, 'Flood Extent')
Map.addLayer(country.style(**style), {}, country_name)
Map

Map(center=[-3.6, -81.5], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=HBox(children…

## Calculate SAR flood area

In [17]:
area_2022 = geemap.zonal_stats(
    water_2022.selfMask(), country, scale=1000, statistics_type='SUM', return_fc=True
)
geemap.ee_to_df(area_2022)

Computing statistics ...


sum        wld_rgn country_na abbreviati country_co
0  28553.364706  South America       Peru                    PE

In [18]:
area_2023 = geemap.zonal_stats(
    water_2023.selfMask(), country, scale=1000, statistics_type='SUM', return_fc=True
)
geemap.ee_to_df(area_2023)

Computing statistics ...


sum        wld_rgn country_na abbreviati country_co
0  25968.941176  South America       Peru                    PE

In [19]:
flood_area = geemap.zonal_stats(
    flood_extent.selfMask(), country, scale=1000, statistics_type='SUM', return_fc=True
)
geemap.ee_to_df(flood_area)

Computing statistics ...


sum        wld_rgn country_na abbreviati country_co
0  2543.003922  South America       Peru                    PE

In [20]:
def export_to_drive_image(file, scale, folder, name):
    task = ee.batch.Export.image.toDrive(
        image = file,
        description = name,
        folder = folder,
        scale = scale, 
        maxPixels = 1e13
    )        # region = country.geometry().bounds().getInfo()['coordinates'], # potentially needed

    task.start()


export_to_drive_image(flood_extent, 100, 'gee', 'sent1_flood_extent_test')